In [1]:
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [2]:
import sys
sys.path.insert(0,'/content/drive/MyDrive/Colab Notebooks/НИР')
home_dir = './drive/MyDrive/Colab Notebooks/НИР'

In [3]:
!pip3 install pyreadr

In [1]:
import pandas as pd
import numpy as np
import torch
from torch.optim import Adam

import pyreadr
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.manifold import TSNE
from mpl_toolkits.mplot3d import Axes3D

from dataset import split_trainValTest
from trainer import train_triplets
from model import VAETriplets

In [2]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

data = pd.read_csv("./Data/Aging_data_scaled_combined_orthologs.csv")
# data.head()
datawNAN = data[data['Species'] == "Mouse"].fillna(0)
datawNAN = torch.Tensor(datawNAN.select_dtypes(include=['float64']).iloc[:, :-1].values)

cpu


In [3]:
batch_size = 64*3
validation_split = .1
test_split = .0
l1_lambda, l2_lambda = 0.03, 0.01
input_size = datawNAN.shape[1] - 1
latent_size = 10
down_channels, up_channels = 2, 2
hidden_size = [10, 20]
lr = 1e-4
epochs = 2000

torch.autograd.set_detect_anomaly(True)

In [4]:
train_loader, val_loader, test_loader = split_trainValTest(datawNAN, batch_size, validation_split, test_split)
vae = VAETriplets(input_size, latent_size, down_channels, up_channels)
vae_optim = Adam(vae.parameters(), lr)
metrics_history, metrics_history_val = train_triplets(vae, train_loader, val_loader, batch_size, epochs, vae_optim, device)


Tracing back tensors:
Tensor with grad found: Parameter containing:
tensor([-0.0091,  0.0384, -0.0012,  ...,  0.0039,  0.0246,  0.0319],
       requires_grad=True)
 - gradient: tensor([ 0.7854, -1.4956, -0.1005,  ...,  0.3279,  0.3009,  0.1784])

Tensor with grad found: Parameter containing:
tensor([-0.1269, -0.1988,  0.1627,  0.0068, -0.0569, -0.0767, -0.1299,  0.1801,
        -0.0849, -0.2862,  0.0440, -0.2018,  0.2434,  0.1135,  0.0079, -0.2981,
        -0.1673, -0.3141, -0.2991, -0.0649, -0.1903, -0.2162,  0.3061, -0.1047,
         0.1815, -0.2980,  0.2603, -0.0671, -0.2727, -0.0953, -0.2595, -0.0214,
         0.0365, -0.0690,  0.0441, -0.1631,  0.2341,  0.0831, -0.2593, -0.2306,
        -0.2518,  0.0847,  0.3030,  0.1221,  0.0409, -0.1709,  0.0307,  0.2334,
         0.1810, -0.2225, -0.0216, -0.1903, -0.0123,  0.1956,  0.0147,  0.2390,
        -0.2473,  0.2501, -0.1943,  0.0302, -0.2295, -0.2463,  0.1239, -0.2327,
        -0.2090,  0.1928,  0.3156,  0.2876, -0.1061, -0.1634, -0.1

Tensor with grad found: Parameter containing:
tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.

 - gradient: tensor([ 2.8409e-01,  2.4921e-01, -3.4006e-01, -7.2668e-01,  1.7026e+00,
         1.1095e+00, -6.3425e-02, -1.0957e+00,  9.9750e-01, -7.5316e-01,
         2.1889e-01,  7.5206e-01,  2.9681e-01, -7.0508e-01, -5.6399e-01,
        -8.4096e-01, -4.4545e-01, -1.1460e+00,  5.2964e-03, -4.3104e-01,
         2.7521e-01,  1.1813e-01, -1.1185e+00,  7.8712e-01,  2.0850e-01,
        -9.0087e-01,  1.8078e-01,  3.8452e-02, -5.6098e-01, -5.8483e-01,
         3.6672e-01, -9.0148e-01, -1.6756e+00,  5.5481e-01,  1.5645e-01,
        -7.5336e-02, -7.4236e-01, -3.2752e-01, -7.2177e-02, -1.8805e-01,
         4.4440e-02,  1.2633e-01,  6.4037e-01,  1.5881e-01,  5.5081e-02,
        -1.0114e+00,  6.8916e-01,  6.2143e-01, -2.1506e-01,  7.7886e-01,
        -6.0687e-01, -6.6294e-02,  4.8858e-02,  3.1002e-01,  7.8960e-01,
        -8.0489e-01, -4.9742e-01,  2.5331e-01,  9.0909e-02,  5.6226e-01,
        -4.6354e-02, -3.0864e-01,  2.3837e-02, -4.7262e-02, -5.9625e-03,
         9.3089e-02,  4.0190e-01, -1.4

 - gradient: tensor([ 1.7509e-07,  1.4901e-08,  1.3039e-08,  3.7253e-09,  4.1351e-07,
        -7.0594e-07, -3.2410e-07, -1.8068e-07, -1.8626e-07,  1.0431e-07,
        -1.4901e-08, -1.6578e-07,  5.0291e-08,  8.5682e-08,  3.0547e-07,
        -1.4901e-08,  1.3970e-07, -1.6764e-07,  1.6764e-08, -3.2596e-08,
         1.4901e-08,  1.4901e-08, -2.2352e-08,  5.3458e-07,  1.8626e-08,
        -8.1956e-08,  1.8068e-07,  9.3132e-10,  1.6950e-07,  2.0489e-08,
        -9.6858e-08,  1.4482e-07,  2.1607e-07,  3.1665e-08,  1.1921e-07,
         3.3528e-08, -5.7742e-08, -1.1642e-07,  1.0245e-08, -3.9116e-08,
         1.1176e-08, -2.9802e-08,  9.0059e-07,  0.0000e+00,  1.3039e-08,
        -4.7288e-07,  1.7881e-07, -7.2271e-07, -3.7253e-09, -9.6858e-08,
         8.3819e-09, -3.7253e-08, -2.5146e-08, -4.6566e-09, -1.6391e-07,
         2.0862e-07, -1.1921e-07, -5.4017e-07,  1.0431e-07,  7.0781e-08,
         1.8161e-08,  2.6077e-08,  1.5832e-08,  4.0978e-08, -7.4506e-08,
         1.3039e-08, -8.1956e-08,  8.1

 - gradient: tensor([ 2.8409e-01,  2.4921e-01, -3.4006e-01, -7.2668e-01,  1.7026e+00,
         1.1095e+00, -6.3425e-02, -1.0957e+00,  9.9750e-01, -7.5316e-01,
         2.1889e-01,  7.5206e-01,  2.9681e-01, -7.0508e-01, -5.6399e-01,
        -8.4096e-01, -4.4545e-01, -1.1460e+00,  5.2964e-03, -4.3104e-01,
         2.7521e-01,  1.1813e-01, -1.1185e+00,  7.8712e-01,  2.0850e-01,
        -9.0087e-01,  1.8078e-01,  3.8452e-02, -5.6098e-01, -5.8483e-01,
         3.6672e-01, -9.0148e-01, -1.6756e+00,  5.5481e-01,  1.5645e-01,
        -7.5336e-02, -7.4236e-01, -3.2752e-01, -7.2177e-02, -1.8805e-01,
         4.4440e-02,  1.2633e-01,  6.4037e-01,  1.5881e-01,  5.5081e-02,
        -1.0114e+00,  6.8916e-01,  6.2143e-01, -2.1506e-01,  7.7886e-01,
        -6.0687e-01, -6.6294e-02,  4.8858e-02,  3.1002e-01,  7.8960e-01,
        -8.0489e-01, -4.9742e-01,  2.5331e-01,  9.0909e-02,  5.6226e-01,
        -4.6354e-02, -3.0864e-01,  2.3837e-02, -4.7262e-02, -5.9625e-03,
         9.3089e-02,  4.0190e-01, -1.4

...

 - gradient: tensor([ 1.7509e-07,  1.4901e-08,  1.3039e-08,  3.7253e-09,  4.1351e-07,
        -7.0594e-07, -3.2410e-07, -1.8068e-07, -1.8626e-07,  1.0431e-07,
        -1.4901e-08, -1.6578e-07,  5.0291e-08,  8.5682e-08,  3.0547e-07,
        -1.4901e-08,  1.3970e-07, -1.6764e-07,  1.6764e-08, -3.2596e-08,
         1.4901e-08,  1.4901e-08, -2.2352e-08,  5.3458e-07,  1.8626e-08,
        -8.1956e-08,  1.8068e-07,  9.3132e-10,  1.6950e-07,  2.0489e-08,
        -9.6858e-08,  1.4482e-07,  2.1607e-07,  3.1665e-08,  1.1921e-07,
         3.3528e-08, -5.7742e-08, -1.1642e-07,  1.0245e-08, -3.9116e-08,
         1.1176e-08, -2.9802e-08,  9.0059e-07,  0.0000e+00,  1.3039e-08,
        -4.7288e-07,  1.7881e-07, -7.2271e-07, -3.7253e-09, -9.6858e-08,
         8.3819e-09, -3.7253e-08, -2.5146e-08, -4.6566e-09, -1.6391e-07,
         2.0862e-07, -1.1921e-07, -5.4017e-07,  1.0431e-07,  7.0781e-08,
         1.8161e-08,  2.6077e-08,  1.5832e-08,  4.0978e-08, -7.4506e-08,
         1.3039e-08, -8.1956e-08,  8.1

Tensor with grad found: Parameter containing:
tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.

 - gradient: tensor([ 2.8409e-01,  2.4921e-01, -3.4006e-01, -7.2668e-01,  1.7026e+00,
         1.1095e+00, -6.3425e-02, -1.0957e+00,  9.9750e-01, -7.5316e-01,
         2.1889e-01,  7.5206e-01,  2.9681e-01, -7.0508e-01, -5.6399e-01,
        -8.4096e-01, -4.4545e-01, -1.1460e+00,  5.2964e-03, -4.3104e-01,
         2.7521e-01,  1.1813e-01, -1.1185e+00,  7.8712e-01,  2.0850e-01,
        -9.0087e-01,  1.8078e-01,  3.8452e-02, -5.6098e-01, -5.8483e-01,
         3.6672e-01, -9.0148e-01, -1.6756e+00,  5.5481e-01,  1.5645e-01,
        -7.5336e-02, -7.4236e-01, -3.2752e-01, -7.2177e-02, -1.8805e-01,
         4.4440e-02,  1.2633e-01,  6.4037e-01,  1.5881e-01,  5.5081e-02,
        -1.0114e+00,  6.8916e-01,  6.2143e-01, -2.1506e-01,  7.7886e-01,
        -6.0687e-01, -6.6294e-02,  4.8858e-02,  3.1002e-01,  7.8960e-01,
        -8.0489e-01, -4.9742e-01,  2.5331e-01,  9.0909e-02,  5.6226e-01,
        -4.6354e-02, -3.0864e-01,  2.3837e-02, -4.7262e-02, -5.9625e-03,
         9.3089e-02,  4.0190e-01, -1.4

Tensor with grad found: Parameter containing:
tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0.

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

